# Carga dos dados na camada Bronze

In [0]:
#Parametro de carga 
dbutils.widgets.text("Ano", "","")
dbutils.widgets.get("Ano")
ParamAno = getArgument("Ano")
ParamAno = str(ParamAno).split(',')

#Parametro de carga 
dbutils.widgets.text("Mês", "","")
dbutils.widgets.get("Mês")
ParamMes= getArgument("Mês")
ParamMes = str(ParamMes).split(',')

In [0]:
import requests
import os
import pandas as pd
from pyspark.sql.functions import current_date, current_timestamp
from pyspark.sql.types import StructType, StructField, IntegerType, DoubleType, StringType, TimestampType

schema = StructType([
    StructField("VendorID", IntegerType(), True),
    StructField("tpep_pickup_datetime", TimestampType(), True),
    StructField("tpep_dropoff_datetime", TimestampType(), True),
    StructField("passenger_count", DoubleType(), True),
    StructField("trip_distance", DoubleType(), True),
    StructField("RatecodeID", DoubleType(), True),
    StructField("store_and_fwd_flag", StringType(), True),
    StructField("PULocationID", IntegerType(), True),
    StructField("DOLocationID", IntegerType(), True),
    StructField("payment_type", IntegerType(), True),
    StructField("fare_amount", DoubleType(), True),
    StructField("extra", DoubleType(), True),
    StructField("mta_tax", DoubleType(), True),
    StructField("tip_amount", DoubleType(), True),
    StructField("tolls_amount", DoubleType(), True),
    StructField("improvement_surcharge", DoubleType(), True),
    StructField("total_amount", DoubleType(), True),
    StructField("congestion_surcharge", DoubleType(), True),
])


anos = ParamAno
meses = ParamMes

local_path = "/mnt/stage/bronze"
for ano in anos:
    for mes in meses:
        url = f"https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_{ano}-{mes}.parquet"
        file_name = f"yellow_tripdata_{ano}-{mes}.parquet"        

        sink_path = f"/mnt/stage/bronze/{ano}/{mes}/"       
        df_pd = pd.read_parquet(url)
        df = spark.createDataFrame(df_pd, schema=schema)

        # Adiciona colunas de carga
        df_bronze = df.withColumn("dt_carga", current_date()) \
                      .withColumn("ts_carga", current_timestamp())
        
        # Salva o DataFrame 
        df_bronze.write.mode('append').format("delta").saveAsTable("table_bronze")        

In [0]:
%sql
select * from table_bronze

VendorID tpep_pickup_datetime tpep_dropoff_datetime passenger_count trip_distance RatecodeID store_and_fwd_flag PULocationID DOLocationID payment_type fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge total_amount congestion_surcharge dt_carga ts_carga 2 2023-03-01T00:06:43Z 2023-03-01T00:16:43Z 1.0 0.0 1.0 N 238 42 2 8.6 1.0 0.5 0.0 0.0 1.0 11.1 0.0 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:08:25Z 2023-03-01T00:39:30Z 2.0 12.4 1.0 N 138 231 1 52.7 6.0 0.5 12.54 0.0 1.0 76.49 2.5 2025-10-01 2025-10-01T15:24:49.8Z 1 2023-03-01T00:15:04Z 2023-03-01T00:29:26Z 0.0 3.3 1.0 N 140 186 1 18.4 3.5 0.5 4.65 0.0 1.0 28.05 2.5 2025-10-01 2025-10-01T15:24:49.8Z 1 2023-03-01T00:49:37Z 2023-03-01T01:01:05Z 1.0 2.9 1.0 N 140 43 1 15.6 3.5 0.5 4.1 0.0 1.0 24.7 2.5 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:08:04Z 2023-03-01T00:11:06Z 1.0 1.23 1.0 N 79 137 1 7.2 1.0 0.5 2.44 0.0 1.0 14.64 2.5 2025-10-01 2025-10-01T15:24:49.8Z 1 2023-03-01T00:09:09Z 2023-03-01T00:17:34Z 1.0 1.2 1.0 N 162 137 1 10.0 3.5 0.5 3.0 0.0 1.0 18.0 2.5 2025-10-01 2025-10-01T15:24:49.8Z 1 2023-03-01T00:32:21Z 2023-03-01T00:42:08Z 1.0 1.8 1.0 N 170 48 1 12.1 3.5 0.5 3.4 0.0 1.0 20.5 2.5 2025-10-01 2025-10-01T15:24:49.8Z 1 2023-03-01T00:45:12Z 2023-03-01T00:52:37Z 1.0 2.0 1.0 N 48 164 2 10.7 3.5 0.5 0.0 0.0 1.0 15.7 2.5 2025-10-01 2025-10-01T15:24:49.8Z 1 2023-03-01T00:19:43Z 2023-03-01T00:39:37Z 1.0 5.3 1.0 N 113 61 1 26.1 3.5 0.5 9.3 0.0 1.0 40.4 2.5 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:08:42Z 2023-03-01T00:18:45Z 1.0 2.27 1.0 N 239 263 1 13.5 1.0 0.5 3.7 0.0 1.0 22.2 2.5 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:48:06Z 2023-03-01T00:57:15Z 1.0 1.95 1.0 N 151 152 2 12.8 1.0 0.5 0.0 0.0 1.0 15.3 0.0 2025-10-01 2025-10-01T15:24:49.8Z 1 2023-03-01T00:10:23Z 2023-03-01T00:13:06Z 1.0 0.8 1.0 N 161 237 1 5.8 3.5 0.5 2.15 0.0 1.0 12.95 2.5 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:22:22Z 2023-03-01T00:32:01Z 5.0 1.17 1.0 N 140 237 2 10.0 1.0 0.5 0.0 0.0 1.0 15.0 2.5 2025-10-01 2025-10-01T15:24:49.8Z 1 2023-03-01T00:01:34Z 2023-03-01T00:16:18Z 1.0 3.6 1.0 N 43 146 1 19.1 3.5 0.5 1.0 0.0 1.0 25.1 2.5 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:09:42Z 2023-03-01T00:15:50Z 1.0 1.42 1.0 N 261 114 1 9.3 1.0 0.5 2.86 0.0 1.0 17.16 2.5 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:45:09Z 2023-03-01T00:49:08Z 1.0 0.53 1.0 N 246 50 1 5.8 1.0 0.5 2.16 0.0 1.0 12.96 2.5 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:55:38Z 2023-03-01T01:06:05Z 1.0 2.22 1.0 N 246 162 1 12.8 1.0 0.5 0.55 0.0 1.0 18.35 2.5 2025-10-01 2025-10-01T15:24:49.8Z 1 2023-03-01T00:10:30Z 2023-03-01T00:13:49Z 1.0 1.0 1.0 N 170 234 1 6.5 3.5 0.5 2.3 0.0 1.0 13.8 2.5 2025-10-01 2025-10-01T15:24:49.8Z 1 2023-03-01T00:20:49Z 2023-03-01T00:30:31Z 1.0 2.0 1.0 N 107 68 4 12.1 3.5 0.5 0.0 0.0 1.0 17.1 2.5 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:29:18Z 2023-03-01T01:06:01Z 2.0 21.03 2.0 N 132 239 1 70.0 0.0 0.5 12.0 6.55 1.0 93.8 2.5 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:34:30Z 2023-03-01T00:46:06Z 1.0 2.8 1.0 N 114 230 1 14.9 1.0 0.5 3.98 0.0 1.0 23.88 2.5 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:02:00Z 2023-03-01T00:23:03Z 1.0 5.63 1.0 N 230 255 1 26.1 1.0 0.5 9.33 0.0 1.0 40.43 2.5 2025-10-01 2025-10-01T15:24:49.8Z 1 2023-03-01T00:09:15Z 2023-03-01T00:37:09Z 1.0 8.4 1.0 N 48 40 1 35.2 3.5 0.5 9.35 6.55 1.0 56.1 2.5 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:11:30Z 2023-03-01T00:27:02Z 1.0 3.76 1.0 N 140 7 1 19.8 1.0 0.5 6.2 0.0 1.0 31.0 2.5 2025-10-01 2025-10-01T15:24:49.8Z 1 2023-03-01T00:50:37Z 2023-03-01T01:04:46Z 1.0 6.4 1.0 N 132 258 1 26.8 2.25 0.5 6.1 0.0 1.0 36.65 0.0 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:25:51Z 2023-03-01T00:55:03Z 1.0 9.5 1.0 N 138 10 1 42.2 6.0 0.5 50.95 0.0 1.0 101.9 0.0 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:11:32Z 2023-03-01T00:26:06Z 1.0 7.73 1.0 N 230 244 1 31.7 1.0 0.5 7.34 0.0 1.0 44.04 2.5 2025-10-01 2025-10-01T15:24:49.8Z 2 2023-03-01T00:47:58Z 2023-03